In [1]:
import mmcv
from mmcv import Config
from mmdet.datasets import (build_dataloader, build_dataset,
                            replace_ImageToTensor)
from mmdet.models import build_detector
from mmdet.apis import single_gpu_test
from mmcv.runner import load_checkpoint
import os
from mmcv.parallel import MMDataParallel
import pandas as pd
from pandas import DataFrame
from pycocotools.coco import COCO
import numpy as np

/opt/conda/envs/project2/lib/python3.7/site-packages/mmcv/__init__.py:21: UserWarning: On January 1, 2023, MMCV will release v2.0.0, in which it will remove components related to the training process and add a data transformation module. In addition, it will rename the package names mmcv to mmcv-lite and mmcv-full to mmcv. See https://github.com/open-mmlab/mmcv/blob/master/docs/en/compatibility.md for more details.
  'On January 1, 2023, MMCV will release v2.0.0, in which it will remove '


In [2]:
classes = ("General trash", "Paper", "Paper pack", "Metal", "Glass", 
           "Plastic", "Styrofoam", "Plastic bag", "Battery", "Clothing")

# config file 들고오기
cfg = Config.fromfile('/opt/ml/level2_objectdetection-cv-11/UniverseNet/configs/tood/tood_swinv2-t-p4-w16_fpn_resize_coco.py')

root='../../dataset/'

epoch = 'best_bbox_mAP_50_epoch_20'

# dataset config 수정
cfg.data.test.classes = classes
cfg.data.test.img_prefix = root
cfg.data.test.ann_file = root + '2___val_MultiStfKFold.json'
cfg.data.test.pipeline[1]['img_scale'] = (1024,1024) # Resize
cfg.data.test.test_mode = True

cfg.data.samples_per_gpu = 4

cfg.seed=2021
cfg.gpu_ids = [1]
cfg.work_dir = '/opt/ml/level2_objectdetection-cv-11/UniverseNet/work_dirs/tood_swinv2-t-p4-w16_fpn_resize_coco_trash'

if "roi_head" in cfg.model.keys():
        if type(cfg.model.roi_head.bbox_head) == dict:
            cfg.model.roi_head.bbox_head.num_classes = 10

        #In case of cascade RCNN : List[Dict]
        elif type(cfg.model.roi_head.bbox_head) == list:
            for each_head in cfg.model.roi_head.bbox_head:
                if hasattr(each_head, "num_classes"):
                    each_head.num_classes = 10 
                else: 
                    raise Exception("Num_classes가 없습니다")
else:
    cfg.model.bbox_head.num_classes = 10
cfg.optimizer_config.grad_clip = dict(max_norm=35, norm_type=2)
cfg.model.train_cfg = None

In [3]:
# build dataset & dataloader
dataset = build_dataset(cfg.data.test)
data_loader = build_dataloader(
        dataset,
        samples_per_gpu=1,
        workers_per_gpu=cfg.data.workers_per_gpu,
        dist=False,
        shuffle=False)

loading annotations into memory...
Done (t=0.01s)
creating index...
index created!


In [4]:
# checkpoint path
checkpoint_path = os.path.join(cfg.work_dir, f'{epoch}.pth')

model = build_detector(cfg.model, test_cfg=cfg.get('test_cfg')) # build detector
checkpoint = load_checkpoint(model, checkpoint_path, map_location='cpu') # ckpt load

model.CLASSES = dataset.CLASSES
model = MMDataParallel(model.cuda(), device_ids=[0])

load checkpoint from local path: /opt/ml/level2_objectdetection-cv-11/UniverseNet/work_dirs/tood_swinv2-t-p4-w16_fpn_resize_coco_trash/best_bbox_mAP_50_epoch_20.pth
The model and loaded state dict do not match exactly

unexpected key in source state_dict: backbone.layers.0.blocks.0.attn.relative_coords_table, backbone.layers.0.blocks.0.attn.relative_position_index, backbone.layers.0.blocks.0.attn.k_bias, backbone.layers.0.blocks.1.attn.relative_coords_table, backbone.layers.0.blocks.1.attn.relative_position_index, backbone.layers.0.blocks.1.attn.k_bias, backbone.layers.1.blocks.0.attn.relative_coords_table, backbone.layers.1.blocks.0.attn.relative_position_index, backbone.layers.1.blocks.0.attn.k_bias, backbone.layers.1.blocks.1.attn.relative_coords_table, backbone.layers.1.blocks.1.attn.relative_position_index, backbone.layers.1.blocks.1.attn.k_bias, backbone.layers.2.blocks.0.attn.relative_coords_table, backbone.layers.2.blocks.0.attn.relative_position_index, backbone.layers.2.blocks

In [5]:
output = single_gpu_test(model, data_loader, show_score_thr=0.05) # output 계산

[                                                  ] 0/977, elapsed: 0s, ETA:

AssertionError: 

In [ ]:
# submission 양식에 맞게 output 후처리
prediction_strings = []
file_names = []
coco = COCO(cfg.data.test.ann_file)
img_ids = coco.getImgIds()

class_num = 10
for i, out in enumerate(output):
    prediction_string = ''
    image_info = coco.loadImgs(coco.getIds(imgIds=[i]))[0]
    for j in range(class_num):
        for o in out[j]:
            prediction_string += str(j) + ' ' + str(o[4]) + ' ' + str(o[0]) + ' ' + str(o[1]) + ' ' + str(
                o[2]) + ' ' + str(o[3]) + ' '
        
    prediction_strings.append(prediction_string)
    file_names.append(image_info['file_name'])


submission = pd.DataFrame()
submission['PredictionString'] = prediction_strings
submission['image_id'] = file_names
submission.to_csv(os.path.join(cfg.work_dir, f'submission_{epoch}_val.csv'), index=None)
submission.head()

loading annotations into memory...
Done (t=0.18s)
creating index...
index created!


IndexError: list index out of range

In [ ]:
output

[[array([[ 9.08294373e+02,  1.64626968e+02,  1.02425513e+03,
           3.88568359e+02,  3.57697785e-01],
         [ 1.16227577e+02,  6.11598999e+02,  1.69057755e+02,
           6.56988342e+02,  3.25146765e-01],
         [ 9.78446228e+02,  9.73762817e+01,  1.02331738e+03,
           1.67754257e+02,  2.40532741e-01],
         [ 9.40905762e+02,  0.00000000e+00,  1.02351178e+03,
           1.10260185e+02,  2.28497967e-01],
         [ 2.48747910e+02,  5.02275970e+02,  2.87646393e+02,
           6.13175354e+02,  2.21305013e-01],
         [ 2.85222839e+02,  1.94269058e+02,  3.43143372e+02,
           2.42602798e+02,  2.12466866e-01],
         [ 5.77277588e+02,  2.73825226e+02,  6.58240051e+02,
           3.39462311e+02,  2.09514603e-01],
         [ 1.05543569e-01,  3.50651611e+02,  4.13182449e+01,
           3.82902130e+02,  2.09406823e-01],
         [ 3.18542969e+02,  3.71923492e+02,  6.53348999e+02,
           5.21288025e+02,  2.09040761e-01],
         [ 5.28767433e+01,  6.65729523e+01,  1